In [1]:
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
import ast
from nltk.tokenize import wordpunct_tokenize, word_tokenize
from nltk.stem.snowball import SnowballStemmer

#### Load in data

In [2]:
data = pd.read_csv('allerhande_preprocessed.csv', index_col=0)
print(data.head())

        id                                   title  \
0   861106            ['vegetarisch', 'bonenstof']   
1   680104                   ['fris', 'limoenrom']   
2   683858  ['kalkoenfilet', 'champignonroomsaus']   
3  1187074     ['andijvie', 'rauw', 'ham', 'prei']   
4   660152        ['spruit', '-', 'rozijnensalad']   

                                         description        course  \
0  ['stoofgerecht', 'vegetarisch', 'balletjes', '...  hoofdgerecht   
1  ['recept', '.', 'nagerecht', 'bevat', 'volgend...     nagerecht   
2  ['kidsprof', 'winter', 'recept', 'pasta', 'kal...  hoofdgerecht   
3  ['bijgerecht', 'andijvie', ',', 'prei', ',', '...    bijgerecht   
4  ['holland', 'recept', '.', 'vegetarisch', 'bij...    bijgerecht   

   recipe_yield                                        ingredients  calories  \
0           4.0  ['olijfolie', 'tomatenblokjes', 'bruine bon', ...     410.0   
1           4.0  ['limoen', 'slagrom', 'vloeibare hon', 'grieks...     290.0   
2           4.

In [3]:
view_data = pd.read_csv('allerhande_raw.csv', index_col=0)
print(view_data.head())
view_data.drop_duplicates(subset='id', inplace=True)

        id                                title  \
0   861106              Vegetarische bonenstoof   
1   680104                    Frisse limoenroom   
2   683858  Kalkoenfilet met champignonroomsaus   
3  1187074       Andijvie met rauwe ham en prei   
4   660152              Spruiten-rozijnensalade   

                                         description        course  \
0  Stoofgerecht met vegetarische balletjes, aarda...  hoofdgerecht   
1  Een lekker recept. Het nagerecht bevat de volg...     nagerecht   
2  Kidsproof winters recept voor pasta met kalkoe...  hoofdgerecht   
3  bijgerecht met andijvie, prei, knoflook, tijm ...    bijgerecht   
4  Een lekker hollands recept. Het vegetarische b...    bijgerecht   

  recipe_yield                                        ingredients calories  \
0   4 personen  {'olijfolie': '2 el()', 'tomatenblokjes': '800...  410kcal   
1   4 personen  {'limoenen': ' 2(schoongeboend)', 'slagroom': ...  290kcal   
2   4 personen  {'olijfolie': '2 el()'

#### Load in inverted columns and convert to dict

In [4]:
inverted_ingredients_pd = pd.read_csv('inverted_list_ingredients.csv', header=None, names=['Word', 'Index'])
print(inverted_ingredients_pd.head())
inverted_ingredients_dict = pd.Series(inverted_ingredients_pd.Index.values,index=inverted_ingredients_pd.Word).to_dict()

                                       Word  \
0                                datterrini   
1                  mexicaanse roerbakgroent   
2                  zachte boter of margarin   
3  stoomgroenten (broccoli/rode ui/paprika)   
4                             bruine suiker   

                                               Index  
0                                             [6320]  
1  [537, 847, 1473, 1544, 2056, 2511, 6391, 6492,...  
2            [3262, 6202, 6579, 13639, 15010, 16674]  
3                                            [10181]  
4  [1442, 2110, 7265, 8615, 9369, 10257, 11532, 1...  


In [5]:
inverted_tags_pd = pd.read_csv('inverted_list_tags.csv', header=None, names=['Word', 'Index'])
# remove row with value NaN
index_nr = []
for i, word in enumerate(inverted_tags_pd['Word']):
    if type(word) is not str:
        index_nr.append(i)
inverted_tags_pd.drop(index_nr, inplace=True)
print(inverted_tags_pd.head())
inverted_tags_dict = pd.Series(inverted_tags_pd.Index.values,index=inverted_tags_pd.Word).to_dict()

                Word                                              Index
1              slank  [0, 45, 67, 135, 172, 221, 260, 344, 369, 386,...
2        advertorial                                       [5741, 7705]
3   sinterklaasavond  [572, 585, 960, 1132, 1583, 1890, 2594, 3162, ...
4        mediterraan  [8, 108, 211, 334, 344, 462, 470, 474, 514, 57...
5              turks  [660, 812, 1294, 1425, 1622, 2150, 2170, 2983,...


In [6]:
inverted_types_pd = pd.read_csv('inverted_list_types.csv', header=None, names=['Word', 'Index'])
print(inverted_types_pd.head())
inverted_types_dict = pd.Series(inverted_types_pd.Index.values,index=inverted_types_pd.Word).to_dict()

        Word                                              Index
0       koek  [102, 134, 228, 648, 690, 749, 888, 976, 1005,...
1  carpaccio  [11, 19, 23, 34, 778, 1285, 1533, 1644, 1796, ...
2         ei  [41, 51, 218, 270, 294, 443, 485, 522, 533, 65...
3  chocolade  [371, 2462, 3250, 4764, 5339, 5858, 7796, 9814...
4   cocktail  [427, 828, 926, 1251, 1558, 1650, 1818, 2000, ...


In [7]:
inverted_title_pd = pd.read_csv('inverted_list_title.csv', header=None, names=['Word', 'Index'])
print(inverted_title_pd.head())
index_nr = []
for i, word in enumerate(inverted_title_pd['Word']):
    if type(word) is not str:
        index_nr.append(i)
print(index_nr)
print(len(inverted_title_pd['Word']))
# print(index_nr)
inverted_title_pd.drop(index_nr, inplace=True)
inverted_title_dict = pd.Series(inverted_title_pd.Index.values,index=inverted_title_pd.Word).to_dict()


            Word   Index
0     peulvrucht  [2591]
1   puntasperges  [3194]
2    advertorial  [7918]
3       pantosti  [6045]
4  kaascroissant  [2751]
[2668]
8694


In [8]:
inverted_course_pd = pd.read_csv('inverted_list_course.csv', header=None, names=['Word', 'Index'])
# remove row with value NaN
inverted_course_pd.drop([4], inplace=True)
print(inverted_course_pd)
inverted_course_dict = pd.Series(inverted_course_pd.Index.values,index=inverted_course_pd.Word).to_dict()

                      Word                                              Index
0             hoofdgerecht  [0, 2, 6, 9, 10, 12, 13, 15, 18, 20, 21, 22, 2...
1   drankje zonder alcohol  [35, 362, 945, 964, 970, 1353, 1366, 1411, 152...
2                  ontbijt  [41, 249, 320, 358, 365, 543, 586, 596, 619, 6...
3             tussendoortj  [230, 257, 673, 690, 789, 1640, 1930, 2258, 24...
5               borrelhapj  [28, 32, 46, 53, 54, 95, 112, 128, 144, 206, 2...
6            kindergerecht  [168, 179, 408, 796, 2114, 2566, 3320, 3552, 3...
7      drankje met alcohol  [263, 324, 427, 662, 828, 871, 1251, 1377, 155...
8                nagerecht  [1, 7, 31, 40, 45, 49, 67, 101, 104, 115, 120,...
9              voorgerecht  [11, 16, 19, 23, 34, 60, 65, 78, 93, 105, 129,...
10                  brunch  [783, 807, 893, 897, 987, 1045, 1305, 1347, 13...
11              bijgerecht  [3, 4, 5, 8, 14, 17, 24, 29, 37, 38, 52, 71, 7...
12                   lunch  [44, 69, 70, 107, 108, 109, 130, 172

#### First for only one word in only one inverted column

In [ ]:
# word = str, inverted_column = dict, retrieved_docs = list
def retrieve_inverted_column(word, inverted_column):
    retrieved_docs = []
    for key in inverted_column.keys():
        if word in key:
            retrieved_docs += ast.literal_eval(inverted_column.get(key))
    return list(set(retrieved_docs))

In [ ]:
print('max tijd', max(data['cooking_time']))
print('max rating', max(data['rating']))
print()

max tijd 1450.0
max rating 5.0



## Retrieval system
- tokenize query, remove all tokens that have len = 1, since these are not words
- for each word in query, create set of documents containing this word
    - look through each inverted column to retrieve possible documents
- get the intersection of the document sets of each word to only retrieve documents with all query words
- print all retrieved documents

- Information from the checkboxes is added to the query words
- Information from the sliders is added to the index sets

In [ ]:
# query = str, inverted_column = list of dicts
def retrieve(query, info_checkbox, info_slider, inverted_columns, dataset):
    tokens = word_tokenize(query)
    words = [item for item in tokens if len(item) > 1]
    
    # lowercase & stemmen
    words = [y.lower() for y in words]
    stemmer = SnowballStemmer("dutch")
    words = [stemmer.stem(y) for y in words]
    words += info_checkbox
    
    set_per_word = []
    
    # loop through query words
    for word in words:
        
        # get set of retrieved docs for each word
        retrieved_docs_word = []
        for column in inverted_columns:
            retrieved_docs_word += retrieve_inverted_column(word, column)
        set_per_word.append(set(retrieved_docs_word))
    
    # get intersection of sets for whole query
    if len(info_slider) > 0:
        retrieved = set(info_slider)
    else:
        retrieved = set_per_word[0]
    for element in set_per_word:
        retrieved = retrieved.intersection(element)
        
    # print all retrieved recipes
    for index in retrieved:
        print(dataset.iloc[index,:])
        print('\n')
        
    return list(retrieved) 
    

In [ ]:
# col_name = str, value = int, max_bool = boolean
def slider_indexes(col_name, value, max_bool, dataset):
    if col_name == 'rating':
        max_bool = False
    if max_bool or (value == 0):
        return []
    # for rating the user wants recipes with **at least** some rating
    elif col_name == 'rating':
        higher = dataset[col_name].values
        return [i for i in range(len(higher)) if higher[i] >= value]
    else:
        lower = dataset[col_name].values
        return [i for i in range(len(lower)) if lower[i] <= value]
    

In [ ]:
test1 = retrieve("ijskoffie", [], [], [inverted_ingredients_dict, inverted_tags_dict, inverted_types_dict, inverted_title_dict],data)
print(test1)
print(data.iloc[test1[0],1])
print(view_data.iloc[test1[0],1])

id                                                               549844
title                                        ['ijskoffie', 'chocorasp']
description           ['recept', '.', 'vegetarisch', 'nagerecht', 'b...
course                                                        nagerecht
recipe_yield                                                          4
ingredients                   ['sterke koffie', 'pure chocolad', 'ijs']
calories                                                            105
protein                                                               2
carbohydrates                                                        12
fat                                                                   6
saturated_fat                                                       NaN
sodium                                                              NaN
fiber                                                               NaN
cooking_time                                                    

## User interface test

In [ ]:
from tkinter import *
from PIL import Image, ImageTk

In [ ]:
### Function to retrieve recipes
def click():
    entered_text = textentry.get()
    
    # Add checkbox info to query
    checkbox_info = []
    if veg.get() == 1:
        checkbox_info.append('vegetarisch')
    if gluten.get() == 1:
        checkbox_info.append('glutenvrij')
    if lacto.get() == 1:
        checkbox_info.append('lactosevrij')
    
    checkbox_info += get_course(course)
    
    # Add slider info indexes
    slider_info = call_slider(scale_list)
    
    results.delete(0, END)
    information.delete(0.0, END)
    global recipes
    recipes = retrieve(entered_text, checkbox_info, slider_info, [inverted_ingredients_dict, inverted_tags_dict, 
                                                     inverted_types_dict, inverted_title_dict, inverted_course_dict],
                       data)
    for i, element in enumerate(recipes):
        results.insert(END, view_data.iloc[element,1])

        
### Function to show additional information for the selected recipe
def show_descr():
    selected_recipe = results.curselection()
    recipe_index = recipes[int(selected_recipe[0])]
    information.delete(0.0, END)
    information.insert(END, "Omschrijving \n", 'big')
    information.insert(END, view_data.iloc[recipe_index,2] + '\n', 'normal')
    information.insert(END, '\nIngrediënten \n', 'big')
    for ingredient in ast.literal_eval(view_data.iloc[recipe_index,5]):
        information.insert(END, ingredient + '\n', 'normal')
        

### Function to retrieved the chosen course
# ontbijt = 1, brunch = 2, lunch = 3, voor = 4, hoofd = 5, na = 6, bij = 7
def get_course(variable):
    value = variable.get()
    if value == 0:
        return []
    if value == 1:
        return ['ontbijt']
    if value == 2:
        return ['brunch']
    if value == 3:
        return ['lunch']
    if value == 4:
        return ['voorgerecht']
    if value == 5:
        return ['hoofdgerecht']
    if value == 6:
        return ['nagerecht']
    if value == 7:
        return ['bijgerecht']

### Function to check the values of all sliders
def call_slider(scales):
    indexes = []
    for i, column in enumerate(['rating', 'calories', 'protein', 'carbohydrates', 'fat', 'saturated_fat', 'sodium',
                                'fiber', 'cooking_time']):
        max_value = False
        slider_val = scales[i].get()
        if slider_val == scales[i].cget("to"):
            max_value = True
        indexes += slider_indexes(column, slider_val, max_value, data)
    return list(set(indexes))
    
    

### General window settings
window = Tk()
window.title('Recepten zoeker v.2')
window.configure(background='white')
window.geometry("{}x{}".format(window.winfo_screenwidth(), window.winfo_screenheight()))

leftframe = Frame(window)
leftframe.pack(side=LEFT)

rightframe = Frame(window)
rightframe.pack(side=RIGHT)

topframe = Frame(rightframe)
topframe.pack()

image = Image.open("bestek.png")
photo1 = ImageTk.PhotoImage(Image.open("bestek.png"))
Label(leftframe, image=photo1).pack()

Label(leftframe, text="Wat wil je eten vanavond?", font='none 24 bold').pack()

middleleft = Frame(leftframe)
middleleft.pack()

### Query box
textentry = Entry(middleleft, width = 50, borderwidth=3)
textentry.pack(side=LEFT)

Button(middleleft, text='Zoek recepten', width=13, command=click, font='none 18 bold').pack(side=LEFT)


### Checkboxes
middleframe = Frame(rightframe)
middleframe.pack()

Label(middleframe, text="Volg je een bepaald dieet?", font='none 13 bold').grid(row=0, column=0, sticky = W)

veg = IntVar()
vegCheck = Checkbutton(middleframe, text='Vegetarisch', variable=veg)
vegCheck.grid(row=1, column=0, sticky=W)

gluten = IntVar()
glutenCheck = Checkbutton(middleframe, text='Glutenvrij', variable=gluten)
glutenCheck.grid(row = 2, column=0, sticky=W)

lacto = IntVar()
lactoCheck = Checkbutton(middleframe, text='Lactosevrij', variable=lacto)
lactoCheck.grid(row = 3, column=0, sticky=W)

Label(middleframe, text='Zoek je naar een specifieke gang?', font='none 13 bold').grid(row=0, column=1, 
                                                                               columnspan=2, sticky=W)

# ontbijt = 1, brunch = 2, lunch = 3, voor = 4, hoofd = 5, na = 6, bij = 7
course = IntVar()
Radiobutton(middleframe, text='Geen voorkeur', variable=course, value=0).grid(row=1, column=1, sticky=W)
Radiobutton(middleframe, text='Ontbijt', variable=course, value=1).grid(row=2, column=1, sticky=W)
Radiobutton(middleframe, text='Brunch', variable=course, value=2).grid(row=3, column=1, sticky=W)
Radiobutton(middleframe, text='Lunch', variable=course, value=3).grid(row=4, column=1, sticky=W)
Radiobutton(middleframe, text='Voorgerecht', variable=course, value=4).grid(row=1, column=2, sticky=W)
Radiobutton(middleframe, text='Hoofdgerecht', variable=course, value=5).grid(row=2, column=2, sticky=W)
Radiobutton(middleframe, text='Nagerecht', variable=course, value=6).grid(row=3, column=2, sticky=W)
Radiobutton(middleframe, text='Bijgerecht', variable=course, value=7).grid(row=4, column=2, sticky=W)


### Sliders
Label(middleframe, text='Gebruik onderstaande sliders om extra informatie aan je zoekopdracht toe te voegen', 
      font='none 13 bold').grid(row=5, column=0, columnspan=3, sticky=E+W)
Label(middleframe, text='Bij geen voorkeur laat je de slider op 0 staan').grid(row=6, column=0, columnspan=3, sticky=E+W)

# 180 means 180-1450
time = Scale(middleframe, from_=0, to=180, length = 180, orient=HORIZONTAL, tickinterval=30, 
             label='Bereidingstijd (min)', font='none 10', sliderlength=15, troughcolor='white')
time.grid(row=7,column=0,sticky=W)

# 1000 means 1000-7680
calories = Scale(middleframe, from_=0, to=1000, length = 180, orient=HORIZONTAL, tickinterval=250, 
             label='Calorieën (kcal)', font='none 10', sliderlength=15, troughcolor='white')
calories.grid(row=8,column=0,sticky=W)

# 20 means 20-400
fiber = Scale(middleframe, from_=0, to=20, length = 180, orient=HORIZONTAL, tickinterval=5, 
             label='Vezels (g)', font='none 10', sliderlength=15, troughcolor='white')
fiber.grid(row=9,column=0,sticky=W)

# 60 means 60-839
protein = Scale(middleframe, from_=0, to=60, length = 180, orient=HORIZONTAL, tickinterval=15, 
             label='Eiwitten (g)', font='none 10', sliderlength=15, troughcolor='white')
protein.grid(row=7,column=1,sticky=W)

# 120 means 120-559
carbo = Scale(middleframe, from_=0, to=120, length = 180, orient=HORIZONTAL, tickinterval=30, 
             label='Koolhydraten (g)', font='none 10', sliderlength=15, troughcolor='white')
carbo.grid(row=8,column=1,sticky=W)

# 2500 means 2500-7655
sodium = Scale(middleframe, from_=0, to=2500, length = 180, orient=HORIZONTAL, tickinterval=600, 
             label='Zout (g)', font='none 10', sliderlength=15, troughcolor='white')
sodium.grid(row=9,column=1,sticky=W)

# 75 means 75-520
fat = Scale(middleframe, from_=0, to=75, length = 180, orient=HORIZONTAL, tickinterval=25, 
             label='Vetten (g)', font='none 10', sliderlength=15, troughcolor='white')
fat.grid(row=7,column=2,sticky=W)

# 35 means 35-755
satur_fat = Scale(middleframe, from_=0, to=35, length = 180, orient=HORIZONTAL, tickinterval=10, 
             label='Verzadigde vetten (g)', font='none 10', sliderlength=15, troughcolor='white')
satur_fat.grid(row=8,column=2,sticky=W)

rating = Scale(middleframe, from_=0, to=5, length = 180, orient=HORIZONTAL, tickinterval=1, 
             label='Rating', font='none 10', sliderlength=15, troughcolor='white')
rating.grid(row=9,column=2,sticky=W)

scale_list = [rating, calories, protein, carbo, fat, satur_fat, sodium, fiber, time]


### Box that shows all retrieved recipes
Label(leftframe, text='Gevonden recepten',font='none 18 bold').pack()
results = Listbox(leftframe, height = 15, width = 75)
results.pack()

Button(leftframe, text="Klik hier om meer informatie te krijgen over het geselecteerde recept", 
       command=show_descr, font='none 16 bold').pack()


### Box that shows additional information about recipe
bottomframe = Frame(rightframe)
bottomframe.pack()

information = Text(bottomframe, width=75, height=20, wrap=WORD)
information.tag_configure('big', font=('none', 14, 'bold'))
information.tag_configure('normal', font=('none', 14))
information.pack(side=LEFT)

window.mainloop()

id                                                               312298
title                              ['gazpacho', 'in', 'borrelglaasjes']
description           ['gazpacho', 'van', 'komkommer', ',', 'tomat',...
course                                                      voorgerecht
recipe_yield                                                          8
ingredients           ['olijfolie extra vierg', 'rode paprika', 'sja...
calories                                                             90
protein                                                               2
carbohydrates                                                         9
fat                                                                   5
saturated_fat                                                         0
sodium                                                              NaN
fiber                                                               NaN
cooking_time                                                    

Name: 10721, dtype: object


id                                                               721590
title                         ['italiaan', 'groentesoep', 'champignon']
description           ['italiaan', 'recept', '.', 'vegetarisch', 'vo...
course                                                      voorgerecht
recipe_yield                                                          4
ingredients           ['olijfolie', 'italiaan', 'kastanjechampignon'...
calories                                                             95
protein                                                               2
carbohydrates                                                         4
fat                                                                   8
saturated_fat                                                       NaN
sodium                                                              NaN
fiber                                                               NaN
cooking_time                       

Name: 14017, dtype: object


id                                                               369646
title                             ['koud', 'avocadosoepj', 'geitenkas']
description           ['recept', '.', 'vegetarisch', 'voorgerecht', ...
course                                                      voorgerecht
recipe_yield                                                          4
ingredients           ['avocado', 'citroenpeper', 'tuinkruidenbouill...
calories                                                            130
protein                                                               2
carbohydrates                                                         5
fat                                                                  10
saturated_fat                                                       NaN
sodium                                                              NaN
fiber                                                               NaN
cooking_time                       

id                                                                99488
title                    ['pittig', 'noedelsoep', 'biefstuk', 'paksoi']
description           ['chines', 'recept', '.', 'hoofdgerecht', 'bev...
course                                                     hoofdgerecht
recipe_yield                                                          4
ingredients           ['sereh', 'zout', 'water', 'bosuitj', 'vleesbo...
calories                                                            345
protein                                                              26
carbohydrates                                                        51
fat                                                                   4
saturated_fat                                                         0
sodium                                                              NaN
fiber                                                               NaN
cooking_time                                                    

Name: 13902, dtype: object


id                                                               733214
title                                          ['biefstuk', 'tagliata']
description           ['biefstuk', 'salad', 'rucola', ',', 'zongedro...
course                                                     hoofdgerecht
recipe_yield                                                          4
ingredients           ['olijfolie', 'geroosterde pijnboompit', 'prem...
calories                                                            455
protein                                                              43
carbohydrates                                                         9
fat                                                                  27
saturated_fat                                                         6
sodium                                                              600
fiber                                                                 2
cooking_time                       

...

id                                                              1030738
title                 ['herfstig', 'boerenkoolstof', 'ei', 'baguet',...
description           ['pittig', 'stoofschotel', 'van', 'boerenkol',...
course                                                     hoofdgerecht
recipe_yield                                                          2
ingredients           ['boter', 'sjalot', 'knoflok', 'rode puntpapri...
calories                                                            790
protein                                                              33
carbohydrates                                                         6
fat                                                                  32
saturated_fat                                                        12
sodium                                                             1825
fiber                                                                13
cooking_time                                                    

id                                                               312298
title                              ['gazpacho', 'in', 'borrelglaasjes']
description           ['gazpacho', 'van', 'komkommer', ',', 'tomat',...
course                                                      voorgerecht
recipe_yield                                                          8
ingredients           ['olijfolie extra vierg', 'rode paprika', 'sja...
calories                                                             90
protein                                                               2
carbohydrates                                                         9
fat                                                                   5
saturated_fat                                                         0
sodium                                                              NaN
fiber                                                               NaN
cooking_time                                                    



id                                                               497738
title                          ['pompoensoep', 'sherry', 'van', 'iren']
description           ['soep', 'van', 'linz', ',', 'pompoen', ',', '...
course                                                     hoofdgerecht
recipe_yield                                                          4
ingredients           ['winterpen', 'laurierblaadj', 'knoflok', 'crè...
calories                                                            425
protein                                                              19
carbohydrates                                                        44
fat                                                                  13
saturated_fat                                                         7
sodium                                                               45
fiber                                                                18
cooking_time                                                  

id                                                               312298
title                              ['gazpacho', 'in', 'borrelglaasjes']
description           ['gazpacho', 'van', 'komkommer', ',', 'tomat',...
course                                                      voorgerecht
recipe_yield                                                          8
ingredients           ['olijfolie extra vierg', 'rode paprika', 'sja...
calories                                                             90
protein                                                               2
carbohydrates                                                         9
fat                                                                   5
saturated_fat                                                         0
sodium                                                              NaN
fiber                                                               NaN
cooking_time                                                    

Name: 7723, dtype: object


id                                                               530442
title                 ['vegetarisch', 'currysoep', '(', 'baby', '9',...
description           ['recept', '.', 'vegetarisch', 'hoofdgerecht',...
course                                                     hoofdgerecht
recipe_yield                                                          2
ingredients           ['ingredienten voor 2 volwassenen, 1 peuter en...
calories                                                            615
protein                                                              20
carbohydrates                                                        53
fat                                                                  35
saturated_fat                                                       NaN
sodium                                                              NaN
fiber                                                               NaN
cooking_time                        